This noteboook uses the SuperBuild of SimpleITK to register a previous subject scan to its corresponding initial reconstruction. The instructions for installing the SuperBuild can be found here:

https://simpleitk.readthedocs.io/en/master/building.html

It is recommended to install the SimpleITK superbuild using a virtual environment. That environment can then be used within a jupyter notebook by adding it as a kernel using the following command:

python -m ipykernel install --user --name=myenv

Where 'myenv' is the name of the environment which contains SimpleITK. The complete instructions for creating and adding a virtual environment in jupyter can be found here:

https://janakiev.com/blog/jupyter-virtual-envs/




In [1]:
import SimpleITK as sitk
import numpy as np
import nibabel as nib
import matplotlib.pyplot as plt
import os

I have created a text file called 'all_files.txt' which contains the pairs of scans that will be registered using this script. The first column of all_files.txt is the previous scan (moving image) and the second column is the initial reconstruction (fixed image). The previous scan will be elastically registered to the initial reconstruction produced in the previous step. 

In [2]:
all_files = np.loadtxt('../data/test_long.txt', dtype=str)
save_path = "../data/reference_reg_10x-iki/"
os.makedirs(save_path, exist_ok=True)

In [3]:
print(all_files)

[['TUM04-20170309.nii' 'TUM04-20171108.nii' 'TUM04-20180103.nii']
 ['TUM04-20171108.nii' 'TUM04-20190328.nii' 'TUM04-20190523.nii']
 ['TUM04-20180618.nii' 'TUM04-20181009.nii' 'TUM04-20190328.nii']
 ['TUM20-20170928.nii' 'TUM20-20180205.nii' 'TUM20-20180402.nii']
 ['TUM10-20170316.nii' 'TUM10-20171018.nii' 'TUM10-20180122.nii']
 ['TUM10-20171018.nii' 'TUM10-20180122.nii' 'TUM10-20180307.nii']
 ['TUM15-20170531.nii' 'TUM15-20170801.nii' 'TUM15-20170816.nii']]


In [5]:
all_files[0][1]

'TUM04-20171108.nii'

In [6]:
#perform elastic registration for each pair of longitudinal scans
for idx in range(len(all_files)):
    for ii in range(2):
        
        fixed_path = f"../data/predicted/10x-iki/{all_files[idx][ii+1][:-4]}_predicted.nii" 
        moving_path = f"../../../data/brain-cancer/{all_files[idx][ii]}"
        print('previous scan:', moving_path)
        print('follow-up scan', fixed_path)
        moving = moving_path.split('/')[-1][:-4]
        fixed = fixed_path.split('/')[-1][:-14]

        previous = nib.load(moving_path).get_fdata()
        next_ = nib.load(fixed_path)
        next_affine = next_.affine
        next_ = next_.get_fdata()
        print('shape of fixed image', nib.load(fixed_path).shape)
        print('shape of moving image', nib.load(moving_path).shape)

        # Loading fixed and moving images
        fixed_image = sitk.ReadImage(fixed_path)
        moving_image = sitk.ReadImage(moving_path)

        elastixImageFilter = sitk.ElastixImageFilter()
        elastixImageFilter.SetFixedImage(fixed_image)
        elastixImageFilter.SetMovingImage(moving_image)
        parameterMapVector = sitk.VectorOfParameterMap()
        parameterMapVector.append(sitk.ReadParameterFile("../data/param_files/Par0000affine.txt"))
        parameterMapVector.append(sitk.ReadParameterFile("../data/param_files/Par0000bspline.txt"))

        elastixImageFilter.SetParameterMap(parameterMapVector)
        elastixImageFilter.Execute()

        # Save image as nifti
        registered = elastixImageFilter.GetResultImage()
        reg = sitk.GetArrayFromImage(registered)
        reg = np.swapaxes(reg,0,2)

        name_reg = "elastic_" + moving + "_" + fixed + '.nii'

        img = nib.Nifti1Image(reg, next_affine)
        nib.save(img, save_path + name_reg)
        sitk.WriteImage(registered,save_path + name_reg)
        print(save_path + name_reg)



previous scan: ../../../data/brain-cancer/TUM04-20170309.nii
follow-up scan ../data/predicted/10x-iki/TUM04-20171108_predicted.nii
shape of fixed image (512, 512, 156)
shape of moving image (512, 512, 164)
Installing all components.
InstallingComponents was successful.

ELASTIX version: 5.000
Command line options from ElastixBase:
-fMask    unspecified, so no fixed mask used
-mMask    unspecified, so no moving mask used
-out      ./
-threads  unspecified, so all available threads are used
  The default value "true" is used instead.

  From elastix 4.8 it defaults to true!
This may change the behavior of your registrations considerably.

Command line options from TransformBase:
-t0       unspecified, so no initial transform used

Reading images...
Reading images took 0 ms.

  A default pyramid schedule is used.
  A default pyramid schedule is used.
  The default value "GeometricalCenter" is used instead.
Transform parameters are initialized as: [1, 0, 0, 0, 1, 0, 0, 0, 1, 9.639167601316

166	-0.986552	22.114434	2.641455	0.019634	1.3
167	-0.951372	23.114434	2.581578	0.012208	1.1
168	-0.990102	22.987890	2.589005	0.014719	1.1
169	-0.955798	22.916792	2.593196	0.020289	1.5
170	-0.960959	23.916792	2.535463	0.019996	1.1
171	-0.975185	23.810877	2.541456	0.018230	1.1
172	-0.955124	23.684333	2.548653	0.014915	1.4
173	-0.948850	24.681807	2.493002	0.020598	1.0
174	-0.962822	24.582406	2.498439	0.019423	0.9
175	-0.936132	25.582406	2.444804	0.016562	0.9
176	-0.975655	25.455862	2.451464	0.018813	1.5
177	-0.985345	25.330010	2.458123	0.011782	0.9
178	-0.937529	25.211825	2.464409	0.017033	0.9
179	-0.928346	25.124901	2.469054	0.016089	2.5
180	-0.944334	24.998357	2.475846	0.022312	0.9
181	-0.970231	25.998357	2.423167	0.013020	0.9
182	-0.979218	25.871813	2.429709	0.015473	0.9
183	-0.943539	26.871813	2.378954	0.015800	0.9
184	-0.971946	27.871813	2.330277	0.013043	0.9
185	-0.980592	27.804233	2.333504	0.017192	0.9
186	-0.956150	28.804233	2.286650	0.014709	0.8
187	-0.929494	28.713705	2.290814	0

396	-0.937553	112.821111	0.851023	0.028842	0.9
397	-0.951965	112.694567	0.851829	0.012248	1.3
398	-0.970389	112.568023	0.852636	0.014718	1.0
399	-0.919587	113.564422	0.846322	0.018611	0.9
400	-0.958043	113.437877	0.847119	0.014222	0.9
401	-0.974818	113.325444	0.847828	0.017146	0.9
402	-0.933950	114.325444	0.841563	0.013844	0.9
403	-0.967897	115.325428	0.835390	0.011590	0.9
404	-0.978595	115.198883	0.836166	0.012121	0.9
405	-0.949468	115.105459	0.836740	0.012591	0.9
406	-0.984952	116.093559	0.830709	0.018492	0.8
407	-0.967518	117.093559	0.824693	0.016602	1.0
408	-0.970336	116.967015	0.825450	0.022336	0.9
409	-0.954650	117.427829	0.822702	0.021072	0.9
410	-0.930846	118.427829	0.816801	0.013396	0.9
411	-0.914719	118.301285	0.817543	0.013573	0.9
412	-0.953198	119.301285	0.811716	0.023226	1.0
413	-0.956626	119.174741	0.812449	0.015940	0.9
414	-0.964865	119.048197	0.813183	0.013422	0.8
415	-0.997812	120.048196	0.807418	0.012052	0.9
416	-0.964963	121.029098	0.801842	0.023413	0.9
417	-0.986614

179	-0.828148	55.509929	1.002391	0.018993	0.8
180	-0.830915	54.981890	1.009357	0.038555	2.5
181	-0.832351	55.980637	0.996261	0.022562	0.8
182	-0.822926	55.565600	1.001662	0.026847	0.8
183	-0.836680	55.031734	1.008695	0.015688	0.9
184	-0.836482	54.489283	1.015943	0.023578	0.8
185	-0.841204	53.946855	1.023296	0.025500	0.8
186	-0.820352	54.934100	1.009992	0.020407	0.8
187	-0.859244	54.843183	1.011203	0.014408	0.8
188	-0.855951	55.692887	0.999999	0.022234	0.9
189	-0.799482	56.492046	0.989687	0.024041	0.9
190	-0.853452	56.572687	0.988658	0.018819	0.9
191	-0.814349	56.037471	0.995527	0.019827	0.9
192	-0.798656	55.494849	1.002588	0.022365	0.9
193	-0.811377	54.953118	1.009739	0.011906	0.9
194	-0.832092	55.938904	0.996802	0.020948	0.9
195	-0.832419	56.933087	0.984086	0.022613	0.8
196	-0.851168	57.927912	0.971682	0.013766	0.8
197	-0.874651	57.403245	0.978185	0.021789	0.8
198	-0.804396	58.381098	0.966135	0.016639	0.9
199	-0.812074	57.863523	0.972476	0.025012	0.8
200	-0.853931	58.819606	0.960827	0

418	-0.875828	115.368928	0.562392	0.010382	0.8
419	-0.840245	116.207764	0.558954	0.027072	0.8
420	-0.826280	116.833279	0.556417	0.025052	0.9
421	-0.821241	117.833207	0.552410	0.029580	1.0
422	-0.861219	118.729330	0.548867	0.020315	1.0
423	-0.846049	119.729330	0.544967	0.031557	1.1
424	-0.840557	119.217527	0.546956	0.024670	1.0
425	-0.829122	118.674800	0.549081	0.019616	1.0
426	-0.796335	119.656667	0.545249	0.022867	1.0
427	-0.822970	119.113946	0.547361	0.023844	1.1
428	-0.817777	120.113943	0.543482	0.019942	1.0
429	-0.833890	120.830085	0.540737	0.011851	1.0
430	-0.806325	120.535864	0.541862	0.012122	1.0
431	-0.856503	120.008403	0.543888	0.024871	1.0
432	-0.811699	120.961202	0.540238	0.018027	1.0
433	-0.847235	121.817485	0.536999	0.019760	1.0
434	-0.828702	122.803679	0.533316	0.019927	1.0
435	-0.837397	123.803358	0.529634	0.025835	1.0
436	-0.849001	124.454167	0.527265	0.019151	1.0
437	-0.823128	125.454145	0.523665	0.024466	1.0
438	-0.844036	126.454140	0.520113	0.032554	0.8
439	-0.829512

...

1017	-0.589262	148.229594	0.008306	16.0
1018	-1.030095	148.150100	0.012981	15.6
1019	-0.526136	148.070719	0.006411	15.7
1020	-0.642346	147.991452	0.007078	15.6
1021	-0.533742	147.912298	0.007300	15.7
1022	-1.093485	147.833257	0.013739	16.0
1023	-0.752718	147.754329	0.010422	16.4
1024	-0.936518	147.675512	0.010142	15.5
1025	-0.837819	147.596808	0.012018	15.9
1026	-0.587503	147.518216	0.009507	15.6
1027	-0.943698	147.439735	0.012790	16.5
1028	-1.051996	147.361365	0.017982	15.7
1029	-0.896172	147.283106	0.012875	15.5
1030	-0.938047	147.204958	0.012327	16.1
1031	-0.464572	147.126920	0.008046	15.8
1032	-0.933925	147.048993	0.015096	15.6
1033	-0.863927	146.971175	0.009700	15.7
1034	-0.466910	146.893468	0.006324	16.0
1035	-0.646573	146.815869	0.005989	15.9
1036	-0.630266	146.738380	0.008311	16.4
1037	-1.109347	146.661000	0.018316	15.8
1038	-0.990459	146.583729	0.010866	15.7
1039	-0.494687	146.506566	0.007389	15.7
1040	-0.781595	146.429511	0.008659	15.8
1041	-0.525028	146.352565	0.008064	15.9


1234	-0.950864	133.263508	0.013690	15.6
1235	-0.723315	133.203650	0.013123	15.9
1236	-0.858748	133.143864	0.010305	15.6
1237	-0.775493	133.084149	0.011018	15.7
1238	-0.754443	133.024506	0.012784	16.6
1239	-0.666432	132.964934	0.008969	17.2
1240	-0.499006	132.905433	0.007812	17.6
1241	-0.965344	132.846003	0.012590	16.7
1242	-0.548835	132.786643	0.005612	17.3
1243	-1.071844	132.727355	0.016397	18.1
1244	-0.684456	132.668137	0.009092	16.9
1245	-1.129527	132.608989	0.016423	17.9
1246	-0.642303	132.549912	0.008218	17.7
1247	-0.702656	132.490904	0.009262	17.3
1248	-0.811862	132.431967	0.011619	17.1
1249	-1.055381	132.373100	0.015852	16.3
1250	-0.561004	132.314302	0.010855	15.6
1251	-0.868728	132.255574	0.012313	15.6
1252	-0.691299	132.196916	0.009369	15.7
1253	-0.893211	132.138326	0.011251	15.7
1254	-0.690863	132.079806	0.011705	15.7
1255	-0.390059	132.021355	0.006898	15.4
1256	-0.954014	131.962973	0.012445	15.8
1257	-1.103164	131.904660	0.015784	15.5
1258	-0.512853	131.846415	0.008511	15.5


1448	-0.948236	121.890301	0.009686	15.8
1449	-0.978461	121.843112	0.012458	15.6
1450	-1.119030	121.795971	0.014270	15.7
1451	-0.599092	121.748879	0.007747	15.5
1452	-0.501315	121.701835	0.006656	15.6
1453	-0.465021	121.654840	0.009124	15.6
1454	-0.941760	121.607893	0.012038	15.7
1455	-1.035006	121.560994	0.011449	15.4
1456	-0.923817	121.514144	0.010182	15.5
1457	-0.980402	121.467342	0.010399	15.5
1458	-1.121336	121.420588	0.018528	15.5
1459	-0.684446	121.373882	0.009011	15.5
1460	-0.527844	121.327223	0.011424	15.6
1461	-0.445822	121.280613	0.005946	16.0
1462	-0.499182	121.234050	0.008325	15.9
1463	-0.446553	121.187535	0.006420	15.5
1464	-0.638071	121.141067	0.007308	15.5
1465	-0.565051	121.094647	0.011071	15.6
1466	-0.644772	121.048274	0.009729	15.6
1467	-0.503651	121.001949	0.006299	15.6
1468	-1.020448	120.955671	0.012177	15.7
1469	-0.861112	120.909440	0.010053	15.6
1470	-0.820369	120.863256	0.009328	16.0
1471	-0.895010	120.817119	0.009782	15.4
1472	-0.668993	120.771029	0.007490	15.7


1656	-0.842144	113.015222	0.010288	15.8
1657	-0.650834	112.976646	0.007496	16.1
1658	-0.418107	112.938105	0.005448	15.5
1659	-1.043371	112.899599	0.015841	15.7
1660	-0.984704	112.861128	0.011726	15.5
1661	-0.807521	112.822692	0.016510	15.6
1662	-0.551807	112.784291	0.007191	15.5
1663	-0.670748	112.745924	0.008539	15.6
1664	-0.104592	112.707593	0.004264	15.7
1665	-0.797900	112.669296	0.009408	15.6
1666	-0.424142	112.631034	0.005621	15.6
1667	-1.124028	112.592806	0.011635	15.7
1668	-0.578769	112.554613	0.008718	15.6
1669	-0.807271	112.516455	0.010938	15.8
1670	-1.049651	112.478331	0.012058	15.3
1671	-0.588253	112.440241	0.011541	16.0
1672	-0.753956	112.402186	0.010392	15.5
1673	-0.865998	112.364165	0.008982	15.5
1674	-1.081703	112.326179	0.018425	15.4
1675	-0.861296	112.288227	0.010059	16.0
1676	-0.870041	112.250309	0.013047	15.3
1677	-1.147682	112.212425	0.018715	15.5
1678	-0.876617	112.174575	0.010444	15.6
1679	-1.005554	112.136759	0.013006	15.5
1680	-1.014178	112.098977	0.013435	15.5


1861	-0.695889	105.774407	0.008275	17.0
1862	-0.532925	105.742073	0.005100	16.5
1863	-0.971706	105.709766	0.012763	16.7
1864	-0.000091	105.677485	0.000109	16.5
1865	-0.100592	105.645230	0.004975	16.2
1866	-0.078292	105.613001	0.002424	17.1
1867	-0.753281	105.580799	0.011816	16.5
1868	-0.622894	105.548623	0.005879	17.0
1869	-0.847773	105.516473	0.009208	16.5
1870	-0.408854	105.484349	0.004953	17.8
1871	-0.880489	105.452251	0.009031	16.6
1872	-1.131173	105.420179	0.014589	16.0
1873	-0.869374	105.388133	0.012238	16.1
1874	-0.936794	105.356113	0.013006	17.3
1875	-0.620241	105.324119	0.008653	16.7
1876	-0.473698	105.292151	0.007521	16.8
1877	-1.178262	105.260209	0.011903	16.5
1878	-0.650483	105.228293	0.009604	16.4
1879	-0.452005	105.196402	0.006779	16.8
1880	-1.012633	105.164537	0.010199	17.1
1881	-0.984278	105.132698	0.012667	16.7
1882	-0.668426	105.100885	0.008278	18.3
1883	-0.724092	105.069097	0.009107	16.6
1884	-0.712724	105.037335	0.008819	16.9
1885	-0.797815	105.005598	0.012724	16.9
